### Imports

In [5]:

import numpy as np #to better use of the arrays

import time #measure time

import matplotlib.pyplot as plt #plots

import pandas as pd #for csv

import seaborn as sns

import subprocess #for write file...
import random
import string
import os
import sys
import shutil
import glob

### Generating

In [6]:
YARPGEN_PATH = '../../bin/yarpgen.out'
SOURCE_FILE = 'driver.c'
BINARY_FILE = 'program'
YARPGEN_DIR_BASE = '../../data/TimeCodeExperiment/traditionalFuzzers/yarpgen/'
CSMITH_DIR_BASE = '../../data/TimeCodeExperiment/traditionalFuzzers/csmith/'
opt_flag = '-O2'

if not os.path.exists(YARPGEN_DIR_BASE):
    os.makedirs(YARPGEN_DIR_BASE)
if not os.path.exists(CSMITH_DIR_BASE):
    os.makedirs(CSMITH_DIR_BASE)


### Pipeline

In [7]:
class GenerationPipeline:

    def __init__(self, output_dir_base: str, fuzzer="yarpgen"):
        self.output_dir_base = output_dir_base
        self.totalTime = 0
        self.totalTries = 0
        self.failures = 0
        self.success = 0
        self.regressions = 0
        self.first_regression_time = 0
        self.fuzzer = fuzzer
        
    def yarpgen_program(self, output_dir: str):
        if not os.path.exists(output_dir):
            os.makedirs(output_dir)
            
        print("[*] Generating program with YARPGen...")
        result = subprocess.run([YARPGEN_PATH, "--std=c", f"--out-dir={output_dir}"])
        if result.returncode != 0:
            print("[!] YARPGen failed")
            sys.exit(1)
            return None
        else:
            print("[*] YARPGen program generated successfully")
            return result.stdout
        
    def csmith_program(self, output_dir: str, source: str):
        if not os.path.exists(output_dir):
            os.makedirs(output_dir)
            
        print("[*] Generating program with Csmith...")
        with open(f"{output_dir}/{source}.c", "w") as output_file:
            result = subprocess.run(["csmith"], stdout=output_file)
        if result.returncode != 0:
            print("[!] Csmith failed")
            sys.exit(1)
            return None
        else:
            print("[*] Csmith program generated successfully")
            return result.stdout
        

    def compile_program(self, source_dir: str, out_dir: str, out_file: str):
        if not os.path.exists(out_dir):
            os.makedirs(out_dir)
            
        opt_flags = ['-O0', '-O1', '-O2', '-O3', '-Os', '-Ofast']
        print("[*] Compiling the program...")
        for opt_flag in opt_flags:
            c_files = glob.glob(f"{source_dir}/*.c")
            result = subprocess.run(["gcc", opt_flag, *c_files, f'-I{source_dir}', "-o", f'{out_dir}/{out_file}{opt_flag}.out'])
            if result.returncode != 0:
                print("[!] Compilation failed")
                self.failures += 1
                return False
        self.success += 1
        return True

    def folder_generator(self, size=4):
        # Geração de nome aleatório para a pasta
        chars = string.ascii_uppercase
        random_name = ''.join(random.choice(chars) for _ in range(size))

        # Verifica se o nome da pasta já existe no diretório local
        while os.path.exists(os.path.join(self.output_dir_base, random_name)):
            random_name = ''.join(random.choice(chars) for _ in range(size))

        # Caminho completo da nova pasta
        folder_path = os.path.join(self.output_dir_base, random_name)

        # Cria a pasta localmente
        os.makedirs(folder_path)

        # Retorna o caminho da pasta criada e o nome aleatório
        return folder_path, random_name
    def get_binary_size(self, file_path):
        if not os.path.exists(file_path):
            return 0
        result = subprocess.run(['size', file_path], capture_output=True, text=True, check=True)
        lines = result.stdout.splitlines()
        
        if len(lines) < 2:
            return 0
        
        parts = lines[1].split()
        return int(parts[0])
    
    def verify_regression(self, binary_dir: str, binary_file: str) -> bool:
        # Verifica se o diretório existe
        if not os.path.exists(binary_dir):
            print(f"Directory {binary_dir} does not exist.")    
            return False
        
        optmization_flags = ['-O0', '-O1', '-O2', '-O3', '-Os', '-Ofast']

        binary_sizes = {}

        for opt_flag in optmization_flags:
            binary_path = os.path.join(binary_dir, f"{binary_file}{opt_flag}.out")
            size = self.get_binary_size(binary_path)
            binary_sizes[opt_flag] = size
            print(f"Binary size for {opt_flag}: {size} bytes")
            
        for opt_flag in optmization_flags:
            if opt_flag != '-Os' and int(binary_sizes['-Os']) - int(binary_sizes[opt_flag]) > 32:
                return True

        # Check for regression
        return False
    
    def generate(self):
        # Inicializa o cronômetro
        start_time = time.time()

        # Aumenta o contador de tentativas
        self.totalTries += 1

        # Cria uma nova pasta com nome aleatório
        folder_path, random_name = self.folder_generator()

        # Gera o programa YARPGen
        match self.fuzzer:
            case "yarpgen":
                self.yarpgen_program(folder_path)
            case "csmith":
                self.csmith_program(folder_path, random_name)

        # Compila o programa gerado
        compiled = self.compile_program(folder_path, folder_path, random_name)
        
        regression = False


        if not compiled:
            shutil.rmtree(folder_path)
        else:
            # Verifica a regressão TODO!
            regression = self.verify_regression(folder_path, random_name)
            if regression:
                self.regressions += 1
                if self.first_regression_time == 0:
                    self.first_regression_time = time.time() - start_time
                print(f"[!] Regression detected in {folder_path}")
            else:
                shutil.rmtree(folder_path)

        # Termina o cronômetro
        end_time = time.time()
        timeSpent = end_time - start_time
        self.totalTime += timeSpent

        # Retorna o caminho da pasta criada e o nome aleatório
        return regression, timeSpent, self.totalTime
    

    def print_status(self):
        print(f"Total time: {self.totalTime:.2f}s")
        print(f"Failures: {self.failures}")
        print(f"Success: {self.success}")
        print(f"Regressions: {self.regressions}")
        if self.regressions > 0:
            print(f"First regression time: {self.first_regression_time:.2f}s")


### Csmith Run

In [ ]:
# pipeline = GenerationPipeline(CSMITH_DIR_BASE, fuzzer="csmith")
# while(pipeline.totalTime < 3600.00):
#     pipeline.generate()

# df = pd.DataFrame({
#     'fuzzer': pipeline.fuzzer,
#     'total_tries': pipeline.totalTries,
#     'total_time': pipeline.totalTime,
#     'failures': pipeline.failures,
#     'success': pipeline.success,
#     'regressions': pipeline.regressions,
#     'first_regression_time': pipeline.first_regression_time
# }, index=[0])

# df.to_csv(f"{CSMITH_DIR_BASE}/results.csv", index=False)

# pipeline.print_status()

[*] Generating program with Csmith...
[*] Csmith program generated successfully
[*] Compiling the program...


../../data/TimeCodeExperiment/traditionalFuzzers/csmith/SYXO/SYXO.c: In function ‘func_9’:
../../data/TimeCodeExperiment/traditionalFuzzers/csmith/SYXO/SYXO.c:269:185: warning: unsigned conversion from ‘long int’ to ‘uint8_t’ {aka ‘unsigned char’} changes value from ‘-63210’ to ‘22’ [-Woverflow]
  269 |     (*l_3132) ^= (((safe_rshift_func_int16_t_s_u(p_13, 14)) , (p_10 , p_10)) <= (((((((func_46((safe_rshift_func_uint16_t_u_s((safe_mod_func_int16_t_s_s(((0L || p_11) <= (((*l_3156) = (~(((safe_sub_func_int8_t_s_s(((((((*l_3153) = (safe_add_func_int32_t_s_s(0x83CBD23FL, (+(*l_3134))))) , l_3154[2][6][4]) == (**g_1610)) , l_3155) != (void*)0), 0x3AL)) > (***g_1617)) , 0xF6E9L))) && 255UL)), p_14)), l_3157[4])), p_14, p_12, l_3158) , 1L) ^ (*p_12)) || (*l_3130)) >= p_14) >= (****g_2367)) && (*l_3136)) , g_3159[0]));
      |                                                                                                                                                                        

Binary size for -O0: 90433 bytes
Binary size for -O1: 16562 bytes
Binary size for -O2: 19030 bytes
Binary size for -O3: 19270 bytes
Binary size for -Os: 15915 bytes
Binary size for -Ofast: 19370 bytes
[*] Generating program with Csmith...
[*] Csmith program generated successfully
[*] Compiling the program...
Binary size for -O0: 16226 bytes
Binary size for -O1: 2019 bytes
Binary size for -O2: 2047 bytes
Binary size for -O3: 2255 bytes
Binary size for -Os: 1948 bytes
Binary size for -Ofast: 2355 bytes
[*] Generating program with Csmith...
[*] Csmith program generated successfully
[*] Compiling the program...


../../data/TimeCodeExperiment/traditionalFuzzers/csmith/KPEG/KPEG.c:86:64: warning: conversion from ‘long unsigned int’ to ‘unsigned int’ changes value from ‘18446744073709551609’ to ‘4294967289’ [-Woverflow]
   86 | static volatile struct S0 g_209 = {0L,7UL,0xA41E839CC648200ALL,18446744073709551609UL};/* VOLATILE GLOBAL g_209 */
      |                                                                ^~~~~~~~~~~~~~~~~~~~~~
../../data/TimeCodeExperiment/traditionalFuzzers/csmith/KPEG/KPEG.c:119:482: warning: conversion from ‘long unsigned int’ to ‘unsigned int’ changes value from ‘18446744073709551615’ to ‘4294967295’ [-Woverflow]
  119 | static struct S0 g_466[9][9][3] = {{{{0x62428E2DC14466C3LL,0x80F45DC1L,0L,1UL},{0xDB01948D6704EC48LL,4294967295UL,-4L,1UL},{0x6E0781368C299D8ELL,0UL,0x970AEC4473471554LL,2UL}},{{0x24E2724D8AFF953ELL,0x812CB51FL,0x55CAACB1BBA240ECLL,0x37F8712BL},{0L,0xA66BEE1DL,-1L,1UL},{0xBA53DFAF08C80EB5LL,1UL,-1L,0x66A0CBC8L}},{{-1L,0x9B32808BL,0xF0EF07622CB6454FLL,0x

Binary size for -O0: 59025 bytes
Binary size for -O1: 16254 bytes
Binary size for -O2: 19023 bytes
Binary size for -O3: 19311 bytes
Binary size for -Os: 15768 bytes
Binary size for -Ofast: 19407 bytes
[*] Generating program with Csmith...
[*] Csmith program generated successfully
[*] Compiling the program...


...

Binary size for -O0: 121060 bytes
Binary size for -O1: 35615 bytes
Binary size for -O2: 46782 bytes
Binary size for -O3: 46942 bytes
Binary size for -Os: 34524 bytes
Binary size for -Ofast: 47042 bytes
[*] Generating program with Csmith...
[*] Csmith program generated successfully
[*] Compiling the program...
Binary size for -O0: 11428 bytes
Binary size for -O1: 1908 bytes
Binary size for -O2: 1997 bytes
Binary size for -O3: 2205 bytes
Binary size for -Os: 1842 bytes
Binary size for -Ofast: 2301 bytes
[*] Generating program with Csmith...
[*] Csmith program generated successfully
[*] Compiling the program...


../../data/TimeCodeExperiment/traditionalFuzzers/csmith/OUQL/OUQL.c:23:43: warning: conversion from ‘long unsigned int’ to ‘unsigned int’ changes value from ‘18446744073709551606’ to ‘4294967286’ [-Woverflow]
   23 | static uint32_t g_5[6][6] = {{0x279C4185L,18446744073709551606UL,0x279C4185L,0x279C4185L,18446744073709551606UL,0x279C4185L},{0x279C4185L,18446744073709551606UL,0x279C4185L,0x279C4185L,18446744073709551606UL,0x279C4185L},{0x279C4185L,18446744073709551606UL,0x279C4185L,0x279C4185L,18446744073709551606UL,0x279C4185L},{0x279C4185L,18446744073709551606UL,0x279C4185L,0x279C4185L,18446744073709551606UL,0x279C4185L},{0x279C4185L,18446744073709551606UL,0x279C4185L,0x279C4185L,18446744073709551606UL,0x279C4185L},{0x279C4185L,18446744073709551606UL,0x279C4185L,0x279C4185L,18446744073709551606UL,0x279C4185L}};
      |                                           ^~~~~~~~~~~~~~~~~~~~~~
../../data/TimeCodeExperiment/traditionalFuzzers/csmith/OUQL/OUQL.c:23:90: warning: conversion from ‘lo

Binary size for -O0: 82617 bytes
Binary size for -O1: 18471 bytes
Binary size for -O2: 21166 bytes
Binary size for -O3: 21438 bytes
Binary size for -Os: 18027 bytes
Binary size for -Ofast: 21538 bytes
[*] Generating program with Csmith...
[*] Csmith program generated successfully
[*] Compiling the program...


../../data/TimeCodeExperiment/traditionalFuzzers/csmith/XAJI/XAJI.c: In function ‘func_1’:
../../data/TimeCodeExperiment/traditionalFuzzers/csmith/XAJI/XAJI.c:280:307: warning: comparison of distinct pointer types lacks a cast
  280 |                         (**l_23) = ((((*g_103) = (((safe_lshift_func_uint8_t_u_u((0x18L < (safe_rshift_func_int16_t_s_u((safe_mul_func_int16_t_s_s((safe_mod_func_uint16_t_u_u((*g_1536), l_2687[5])), (safe_sub_func_uint8_t_u_u(((2UL >= (((**g_2336) , g_2794[2][0]) , (safe_lshift_func_uint8_t_u_s(((&g_2503 != l_2797) ^ (**g_1535)), l_2799)))) ^ 0xF88CL), l_2799)))), l_2687[2]))), 6)) || l_2800) , 0x499F9DD14846FE1FLL)) ^ l_2685) , (-1L));
      |                                                                                                                                                                                                                                                                                                                   ^~
../../d

Binary size for -O0: 106639 bytes
Binary size for -O1: 12787 bytes
Binary size for -O2: 17182 bytes
Binary size for -O3: 17358 bytes
Binary size for -Os: 11971 bytes
Binary size for -Ofast: 17458 bytes
[*] Generating program with Csmith...


In [8]:
pipeline = GenerationPipeline(YARPGEN_DIR_BASE, fuzzer="yarpgen")
while(pipeline.totalTime < 3600.00):
    pipeline.generate()

df = pd.DataFrame({
    'fuzzer': pipeline.fuzzer,
    'total_tries': pipeline.totalTries,
    'total_time': pipeline.totalTime,
    'failures': pipeline.failures,
    'success': pipeline.success,
    'regressions': pipeline.regressions,
    'first_regression_time': pipeline.first_regression_time
}, index=[0])

df.to_csv(f"{YARPGEN_DIR_BASE}/results.csv", index=False)

pipeline.print_status()

[*] Generating program with YARPGen...
/*SEED 527802889*/
[*] YARPGen program generated successfully
[*] Compiling the program...
Binary size for -O0: 5532 bytes
Binary size for -O1: 4466 bytes
Binary size for -O2: 4526 bytes
Binary size for -O3: 7047 bytes
Binary size for -Os: 3759 bytes
Binary size for -Ofast: 7135 bytes
[*] Generating program with YARPGen...
/*SEED 2053599516*/
[*] YARPGen program generated successfully
[*] Compiling the program...
Binary size for -O0: 2039 bytes
Binary size for -O1: 1807 bytes
Binary size for -O2: 1888 bytes
Binary size for -O3: 1888 bytes
Binary size for -Os: 1777 bytes
Binary size for -Ofast: 1988 bytes
[*] Generating program with YARPGen...
/*SEED 3365222708*/
[*] YARPGen program generated successfully
[*] Compiling the program...
Binary size for -O0: 10395 bytes
Binary size for -O1: 7029 bytes
Binary size for -O2: 7515 bytes
Binary size for -O3: 28749 bytes
Binary size for -Os: 5937 bytes
Binary size for -Ofast: 28845 bytes
[*] Generating progr

/tmp/ccdlaN09.o: na função "init":
driver.c:(.text+0x91f): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_15" na seção .bss em /tmp/ccdlaN09.o
driver.c:(.text+0x9dd): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_12" na seção .bss em /tmp/ccdlaN09.o
driver.c:(.text+0xad6): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_16" na seção .bss em /tmp/ccdlaN09.o
driver.c:(.text+0xbf0): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_17" na seção .bss em /tmp/ccdlaN09.o
driver.c:(.text+0xc62): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_18" na seção .bss em /tmp/ccdlaN09.o
driver.c:(.text+0xcb6): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_19" na seção .bss em /tmp/ccdlaN09.o
driver.c:(.text+0xd13): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_20" na seção .bss em /

[!] Compilation failed
[*] Generating program with YARPGen...
/*SEED 3002142680*/
[*] YARPGen program generated successfully
[*] Compiling the program...


/tmp/cc5ZcmoF.o: na função "init":
driver.c:(.text+0x1502): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_24" na seção .bss em /tmp/cc5ZcmoF.o
driver.c:(.text+0x15c4): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_25" na seção .bss em /tmp/cc5ZcmoF.o
driver.c:(.text+0x1668): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_28" na seção .bss em /tmp/cc5ZcmoF.o
driver.c:(.text+0x1780): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_32" na seção .bss em /tmp/cc5ZcmoF.o
driver.c:(.text+0x1891): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_35" na seção .bss em /tmp/cc5ZcmoF.o
driver.c:(.text+0x196e): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_36" na seção .bss em /tmp/cc5ZcmoF.o
/tmp/cc5ZcmoF.o: na função "checksum":
driver.c:(.text+0x2333): realocação truncada para caber: R_X86_64_PC32 contra sí

[!] Compilation failed
[*] Generating program with YARPGen...
/*SEED 2127131054*/
[*] YARPGen program generated successfully
[*] Compiling the program...
Binary size for -O0: 1986 bytes
Binary size for -O1: 1766 bytes
Binary size for -O2: 1870 bytes
Binary size for -O3: 1870 bytes
Binary size for -Os: 1722 bytes
Binary size for -Ofast: 1970 bytes
[*] Generating program with YARPGen...
/*SEED 1273367853*/
[*] YARPGen program generated successfully
[*] Compiling the program...
Binary size for -O0: 5895 bytes
Binary size for -O1: 4628 bytes
Binary size for -O2: 5346 bytes
Binary size for -O3: 6847 bytes
Binary size for -Os: 4025 bytes
Binary size for -Ofast: 6931 bytes
[*] Generating program with YARPGen...
/*SEED 2798431197*/
[*] YARPGen program generated successfully
[*] Compiling the program...
Binary size for -O0: 3323 bytes
Binary size for -O1: 2698 bytes
Binary size for -O2: 2869 bytes
Binary size for -O3: 7395 bytes
Binary size for -Os: 2492 bytes
Binary size for -Ofast: 7465 bytes

...

[!] Compilation failed
[*] Generating program with YARPGen...
/*SEED 3097118329*/
[*] YARPGen program generated successfully
[*] Compiling the program...
[!] Compilation failed
[*] Generating program with YARPGen...
/*SEED 3912109820*/
[*] YARPGen program generated successfully
[*] Compiling the program...
Binary size for -O0: 1858 bytes
Binary size for -O1: 1700 bytes
Binary size for -O2: 1763 bytes
Binary size for -O3: 1763 bytes
Binary size for -Os: 1675 bytes
Binary size for -Ofast: 1863 bytes
[*] Generating program with YARPGen...
/*SEED 1945821336*/
[*] YARPGen program generated successfully
[*] Compiling the program...
Binary size for -O0: 1869 bytes
Binary size for -O1: 1733 bytes
Binary size for -O2: 1836 bytes
Binary size for -O3: 1836 bytes
Binary size for -Os: 1706 bytes
Binary size for -Ofast: 1936 bytes
[*] Generating program with YARPGen...
/*SEED 1557210831*/
[*] YARPGen program generated successfully
[*] Compiling the program...


/tmp/ccZYKqq7.o: na função "init":
driver.c:(.text+0x9c6): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_18" na seção .bss em /tmp/ccZYKqq7.o
driver.c:(.text+0xb00): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_19" na seção .bss em /tmp/ccZYKqq7.o
driver.c:(.text+0xbf9): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_26" na seção .bss em /tmp/ccZYKqq7.o
driver.c:(.text+0xcb6): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_27" na seção .bss em /tmp/ccZYKqq7.o
driver.c:(.text+0xd85): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_34" na seção .bss em /tmp/ccZYKqq7.o
driver.c:(.text+0xe6f): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_35" na seção .bss em /tmp/ccZYKqq7.o
driver.c:(.text+0xf79): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_36" na seção .bss em /

[!] Compilation failed
[*] Generating program with YARPGen...
/*SEED 3337198688*/
[*] YARPGen program generated successfully
[*] Compiling the program...
Binary size for -O0: 5304 bytes
Binary size for -O1: 3806 bytes
Binary size for -O2: 4071 bytes
Binary size for -O3: 15028 bytes
Binary size for -Os: 3335 bytes
Binary size for -Ofast: 15124 bytes
[*] Generating program with YARPGen...
/*SEED 3456970984*/
[*] YARPGen program generated successfully
[*] Compiling the program...
Binary size for -O0: 2015 bytes
Binary size for -O1: 1804 bytes
Binary size for -O2: 1880 bytes
Binary size for -O3: 1880 bytes
Binary size for -Os: 1777 bytes
Binary size for -Ofast: 1980 bytes
[*] Generating program with YARPGen...
/*SEED 1157520133*/
[*] YARPGen program generated successfully
[*] Compiling the program...
Binary size for -O0: 1820 bytes
Binary size for -O1: 1690 bytes
Binary size for -O2: 1750 bytes
Binary size for -O3: 1750 bytes
Binary size for -Os: 1663 bytes
Binary size for -Ofast: 1850 byt

/tmp/ccT4pKgF.o: na função "init":
driver.c:(.text+0x315a): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_107" na seção .bss em /tmp/ccT4pKgF.o
driver.c:(.text+0x327a): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_108" na seção .bss em /tmp/ccT4pKgF.o
driver.c:(.text+0x3331): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_111" na seção .bss em /tmp/ccT4pKgF.o
driver.c:(.text+0x3415): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_12" na seção .bss em /tmp/ccT4pKgF.o
driver.c:(.text+0x356e): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_16" na seção .bss em /tmp/ccT4pKgF.o
driver.c:(.text+0x3609): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_19" na seção .bss em /tmp/ccT4pKgF.o
driver.c:(.text+0x36d3): realocação truncada para caber: R_X86_64_PC32 contra símbolo não definido "arr_22" na seção

[!] Compilation failed
[*] Generating program with YARPGen...
/*SEED 1171478854*/
[*] YARPGen program generated successfully
[*] Compiling the program...
Binary size for -O0: 5143 bytes
Binary size for -O1: 3330 bytes
Binary size for -O2: 3723 bytes
Binary size for -O3: 4154 bytes
Binary size for -Os: 2965 bytes
Binary size for -Ofast: 4270 bytes
[*] Generating program with YARPGen...
/*SEED 4207131752*/
[*] YARPGen program generated successfully
[*] Compiling the program...
Binary size for -O0: 2295 bytes
Binary size for -O1: 1871 bytes
Binary size for -O2: 1983 bytes
Binary size for -O3: 1983 bytes
Binary size for -Os: 1833 bytes
Binary size for -Ofast: 2083 bytes
[*] Generating program with YARPGen...
/*SEED 3441981617*/
[*] YARPGen program generated successfully
[*] Compiling the program...
Binary size for -O0: 2153 bytes
Binary size for -O1: 1911 bytes
Binary size for -O2: 2031 bytes
Binary size for -O3: 2031 bytes
Binary size for -Os: 1859 bytes
Binary size for -Ofast: 2131 bytes